In [13]:
import os
import pickle
import numpy as np

from algos import *
from infect import infect
from sbm import SBM

In [14]:
def iter(N, M, q0, q1, p0, p1, time_steps, num_sims, method, dataset='sbm'):
    name = dataset + 'N' + str(N) + '_M' + str(M) + '_SIM' + str(num_sims) + '_step' + str(time_steps) + '_q0' + str(q0) + '_q1' + str(q1) + '_p0' + str(p0) + '_p1' + str(p1) + method + 'graphs.pkl'
    
    if not os.path.isfile(name):
        print('Generating synthetic dataset!')
        Gs = np.zeros((num_sims, N, N))
        Communities = dict()
        data = dict()
        Individuals = dict()
        
        if dataset == 'sbm':
            for i in range(num_sims):
                Gs[i] = SBM(N, M, q0, q1)
                
                 ###################################################
                # Detect communities
                communities = [[] for _ in range(M)]
                community_membership = np.random.choice(M, N)
                for idx, community in enumerate(community_membership):
                    communities[community].append(idx)
                 ###################################################
                 
                Communities[i] = communities
                Individuals[i] = infect(Gs[i], p0, p1, time_steps)
                
        elif dataset == 'iid':
            for i in range(num_sims):
                 ###################################################
                individuals = np.random.binomial(1, p0, N)
                Communities[i] = [list(range(N))]  # Single community with all individuals
                Individuals[i] = infect(Gs[i], p0, p1, time_steps)
                 ###################################################
        data['graph'] = Gs
        data['communities'] = Communities
        data['individuals'] = Individuals
        
        with open(name, 'wb') as infile:
            pickle.dump(data, infile)
    
    if os.path.isfile(name):
        with open(name, 'rb') as infile:
            data = pickle.load(infile)
        print('Data loaded!')
     ###################################################
    fraction_ppl = 0
    fraction_family = 0
    fraction_ppl_in_family = 0
    num_tests = 0
    num_stages = 0
     ###################################################
    num_tests_list = []
    num_stages_list = []

    for i in range(num_sims):
        G = data['graph'][i]
        communities = data['communities'][i]
        individuals = data['individuals'][i]
        
        # Interleave the individuals
        s = individuals.copy()
        np.random.shuffle(s)
        
        # Binary Splitting
        numtests_bs, num_stages_bs, _ = binary_splitting(s)
        
        # Qtesting1
        numtests_q1, num_stages_q1 = Qtesting1(s)
        
        # Qtesting2
        numtests_q2, num_stages_q2 = Qtesting2(s)
        
        # Community-Aware Qtesting1
        numtests_q1_c, num_stages_q1_c = Qtesting1_comm_aware(individuals.copy(), communities)
        
        # Community-Aware Qtesting2
        numtests_q2_c, num_stages_q2_c = Qtesting2_comm_aware(individuals.copy(), communities)
        
         ###################################################
        # Collect statistics
        num_tests_list.append({
            'binary': numtests_bs,
            'q1': numtests_q1,
            'q2': numtests_q2,
            'q1_comm': numtests_q1_c,
            'q2_comm': numtests_q2_c
        })
        
        num_stages_list.append({
            'binary': num_stages_bs,
            'q1': num_stages_q1,
            'q2': num_stages_q2,
            'q1_comm': num_stages_q1_c,
            'q2_comm': num_stages_q2_c
        })
    
    # Calculate averages
    avg_num_tests = {key: np.mean([x[key] for x in num_tests_list]) for key in num_tests_list[0]}
    avg_num_stages = {key: np.mean([x[key] for x in num_stages_list]) for key in num_stages_list[0]}
     ###################################################
    return avg_num_tests, avg_num_stages

# Example usage
N = 264
M = 16
q0 = 0.9
q1 = 0.1
p0 = 0.001
p1 = 0.05
time_steps = 2
num_sims = 100
method = 'Q1_Q2'

avg_num_tests, avg_num_stages = iter(N, M, q0, q1, p0, p1, time_steps, num_sims, method, dataset='sbm')
print(f"Average number of tests: {avg_num_tests}")
print(f"Average number of stages: {avg_num_stages}")


Data loaded!
[[155.   0.   0.]
 [ 92.   0.   0.]
 [106.   0.   0.]
 [114.   0.   0.]
 [124.   0.   0.]
 [233.   0.   0.]
 [170.   0.   0.]
 [230.   0.   0.]
 [221.   0.   0.]
 [ 21.   0.   0.]
 [ 14.   0.   0.]
 [236.   0.   0.]
 [ 13.   0.   0.]
 [ 90.   0.   0.]
 [245.   0.   0.]
 [263.   0.   0.]
 [ 71.   0.   0.]
 [149.   0.   0.]
 [250.   0.   0.]
 [137.   0.   0.]
 [ 42.   0.   0.]
 [ 97.   0.   0.]
 [ 49.   0.   0.]
 [201.   0.   0.]
 [120.   0.   0.]
 [161.   0.   0.]
 [188.   0.   0.]
 [ 69.   0.   0.]
 [ 39.   0.   0.]
 [ 68.   0.   0.]
 [139.   0.   0.]
 [ 96.   0.   0.]
 [ 25.   0.   0.]
 [214.   0.   0.]
 [226.   0.   0.]
 [ 58.   0.   0.]
 [235.   0.   0.]
 [128.   0.   0.]
 [ 23.   0.   0.]
 [  9.   0.   0.]
 [ 95.   0.   0.]
 [140.   0.   0.]
 [ 84.   0.   0.]
 [103.   0.   0.]
 [225.   0.   0.]
 [178.   0.   0.]
 [ 64.   0.   0.]
 [  3.   0.   0.]
 [112.   0.   0.]
 [227.   0.   0.]
 [ 10.   0.   0.]
 [157.   0.   0.]
 [171.   0.   0.]
 [ 60.   0.   0.]
 [ 66.   0.   0

<div class="alert alert-warning">
<b>Task 1 </b> 
Plot how the fraction of infected people, the percentage of infected communities, and the average percentage of infected people in each community change with the each setting for the synthetic dataset described in the following table and comment on the results. Average over at least $100$ SBM network realization.     

</div>

| N | M | q0, q1 | p0 | p1 |time steps  |
|---|---|--------|----|----|------------|
|256| 16| (1,0)  |0.001|[0.05:1]|2|
|   | 16|(0.9, 0.1)  | 0.001| [0.05:1]|2     |
|   | 16 |(0.5, 0.2)  | 0.001| [0.05:1]|2     |

Consider $N=256$, and $M=16,64,128$. Use SBM with $q0=1$ and $q1=0$ to generate contact networks (disconnected cliques). For the infection model, use $p_0 = 0.001$ and $p_1 = [0.01:1]$ and the number of infection steps as $2$ . 
Average over 100 SBM network realizations.

<div class="alert alert-warning">
<b>Task 2 </b> 
Provide plots for i.i.d. infection probability that ranges from $p=0.01$ to $p=0.3$, and $N=256$.
Compare the performance of tests $T_1$, $T_2$, and binary output tests. Do you observe a consistent performance? Can you explain your results? 
    
</div>

<div class="alert alert-warning">
<b>Task 3 </b>  
Provide plots that compare the performance of various testing techniques on the Stochastic Block Model (SBM) using the settings outlined in Table 2 and on real data. You may explore additional settings that could reveal significant insights for your custom algorithms. Interpret and explain the results you obtain. Your plots should include: (i) a plot demonstrating how the performance of different testing schemes varies as the family sizes change, (ii)a plot demonstrating how the performance of different testing schemes varies as the infection probability changes and (iii) a plot illustrating how infections concentrate within families in the SBM.
</div>

| N | M | q0, q1 | p0 | p1 |time steps  |
|---|---|--------|----|----|------------|
|256| 16| (0.9,0.1)  |0.001|[0.05:1]|2|
|   | 64|(1, 0)  | 0.001| [0.05:1]|2     |
|   | 64|(0.9, 0.1)  | 0.001| [0.05:1]|2     |
|   | 64|(0.5, 0.2)  | 0.001| [0.05:1]|2     |
|   | 128 |(0.9, 0.1)  | 0.001| [0.05:1]|2     |


In [ ]:
N = 256
M = 16
q0 = 0.5
q1 = 0.3

time_steps = 2
method = 'your method'

In [11]:
# the simulation 
t = 10
fraction_infected_ppl = np.zeros(t)
fraction_infected_clc = np.zeros(t)
fraction_infected_family = np.zeros(t)
num_tests = np.zeros((t,3))
num_stages = np.zeros((t,3))
p0 = 0.001
num_sims = 100
for j in range(1,t+1):
    p1 = j/t
    fraction_ppl[j-1], fraction_clc[j-1], fraction_plp_in_clc[j-1], num_tests[j-1], num_stages[j-1]= iter(N,M,q0,q1,p0,p1,time_steps,num_sims,method,dataset='sbm')  
       

NameError: name 'N' is not defined

In [ ]:
p1s = np.arange(1,t+1)/t

In [ ]:
plt.figure(figsize=(6, 4), dpi=300)
plt.rcParams.update({
    'font.size': 12,
    'font.family': 'sans-serif',
    'font.sans-serif': 'Arial',
    'axes.labelsize': 12,
    'xtick.labelsize': 10,
    'ytick.labelsize': 10
})
markers = ['.', ',','o','v','^','<','>']
   
plt.plot(p1s,num_tests[:,i],label='binary splitting',marker=markers[i])
#########your code here###########

plt.xlabel('Transmission probability: p1',fontsize=14)
plt.ylabel('Expected number of tests',fontsize=14)
plt.legend()
plt.grid(True, linestyle='--', linewidth=0.5, color='gray', alpha=0.5)
plt.legend(frameon=False, loc='best')
plt.tight_layout()
fig_name = 'RES_N'+str(N)+'_M'+str(M)+'SIM'+str(num_sims)+'step_'+str(time_steps)+'q0'+str(q0)+'q1'+str(q1)+'p0'+str(p0)+method+'GT.pdf'
plt.savefig(fig_name, format='pdf', bbox_inches='tight')

In [ ]:
plt.plot(p1s,fraction_ppl,label='Fraction of infected people')
plt.plot(p1s,fraction_clc,label='Fraction of infected communities')
plt.plot(p1s,fraction_plp_in_clc,label='Fraction of infected people in each community')
plt.xlabel('Transmission probability: p1',fontsize=14)
plt.ylabel('Infection stats',fontsize=14)
plt.legend()
plt.savefig('RES_N'+str(N)+'_M'+str(M)+'SIM'+str(num_sims)+'step_'+str(time_steps)+'q0'+str(q0)+'q1'+str(q1)+'p0'+str(p0)+method+'stats.pdf')